In [1]:
from bs4 import BeautifulSoup
from fnmatch import fnmatch
from PIL import Image
from PIL import ImageFile
from pathlib import Path
from shutil import copyfile

import imagehash
import mysql.connector
import os
import re

In [2]:
# GENERAL CONFIGS
ImageFile.LOAD_TRUNCATED_IMAGES = True

# == Database config ==
conn = mysql.connector.connect(
  host="localhost",
  user="root",
  password="root"
)

cursor = conn.cursor()

DB_NAME = "blp_dataset"
TABLE_NAME = "products_tmp_hydra"


# == Files config ==
MAIN_FOLDER = r"D:\dnmarchives\dnmarchives\hydra"

In [3]:
# Creating environment
cursor.execute("CREATE DATABASE IF NOT EXISTS {} DEFAULT CHARACTER SET 'utf8'".format(DB_NAME))
cursor.execute("USE {}".format(DB_NAME))

In [4]:
table_schema = (
    "CREATE TABLE IF NOT EXISTS products_tmp_hydra ("
    "  id INT(11) AUTO_INCREMENT PRIMARY KEY NOT NULL,"
    "  name TEXT NOT NULL,"
    "  description TEXT,"
    "  market_name VARCHAR(255),"
    "  seller_name TEXT,"
    "  illegal ENUM('t', 'f') NOT NULL DEFAULT 't'"
    ") ENGINE=InnoDB")

cursor.execute(table_schema)

In [5]:
def get_content(content):
    clear_content = ""

    if content is not None:
        raw_c = content.text

        clear_content = re.sub(r'[\t\r\n]', ' ', raw_c)
        clear_content = re.sub(' +',' ', clear_content).lstrip()
        
    return clear_content

In [6]:
original_images = []

folders = [x for x in Path(MAIN_FOLDER).iterdir() if x.is_dir()]

for fo in folders:
    folder = Path(f"{fo}\sale")
    folder_image = Path(f"{fo}")

    if folder.exists():
        for file in os.listdir(folder):
            print(Path(f"{folder}\{file}"))

            page_content = BeautifulSoup(open(Path(f"{folder}\{file}"), encoding='utf8').read())

            if page_content is not None:
                ## GET DESCRIPTION
                description = ""
                desc_content = page_content.find("pre")

                if desc_content is not None:
                    description = get_content(desc_content)

                ## GET TITLE
                title = ""
                raw_title = page_content.findAll("div", attrs={"class": "widget-head"})

                if raw_title is not None:
                    try:
                        title = get_content(raw_title[0])
                    except:
                        title = ""

                ## GET SELLER
                seller = ""
                seller_content = page_content.find("div", attrs={"class": "span6 well bblue"})

                if seller_content is not None:
                    seller_a = seller_content.findAll("a")
                    
                    if seller_a is not None:
                        seller_raw = seller_a[0]

                        if seller_raw is not None:
                            seller = get_content(seller_raw)

                if description != "" or title != "":
                    # Insert product into database
                    query = "INSERT INTO products_tmp_hydra (name, description, market_name, seller_name, illegal) VALUES (%s, %s, %s, %s, %s)"
                    values = (title, description, "Hydra", seller, "t")

                    cursor.execute(query, values)
                    conn.commit()

                    product_id = cursor.lastrowid

                    ## GET IMAGE
                    raw_name = page_content.find("img", attrs={"class": "img-polaroid"})
                    name = ""

                    if raw_name is not None:
                        try:
                            name = raw_name["src"]
                        except IndexError:
                            print(f"Image {product_id} has no src")

                    if name is not "":
                        url_image = Path(f"{folder_image}\{name}")

                        try:
                            # copy images to new directory, renaming with product id
                            if url_image.exists():
                                print(f"Image {product_id} exists... creating")

                                dst_dir = Path(f"D:\images\_hydra\{product_id}.jpeg")
                                copyfile(url_image, dst_dir)
                            else:
                                print(f"Image {product_id} does not exists")
                        except:
                            print(f"Image {product_id} has error. Except")
                    else:
                        print(f"Image {product_id} has no name")


D:\dnmarchives\dnmarchives\hydra\2014-04-03\sale\10.html
Image 1 exists... creating
D:\dnmarchives\dnmarchives\hydra\2014-04-03\sale\100.html
Image 2 exists... creating
D:\dnmarchives\dnmarchives\hydra\2014-04-03\sale\101.html
Image 3 exists... creating
D:\dnmarchives\dnmarchives\hydra\2014-04-03\sale\102.html
Image 4 exists... creating
D:\dnmarchives\dnmarchives\hydra\2014-04-03\sale\103.html
Image 5 exists... creating
D:\dnmarchives\dnmarchives\hydra\2014-04-03\sale\104.html
Image 6 exists... creating
D:\dnmarchives\dnmarchives\hydra\2014-04-03\sale\105.html
Image 7 exists... creating
D:\dnmarchives\dnmarchives\hydra\2014-04-03\sale\106.html
Image 8 exists... creating
D:\dnmarchives\dnmarchives\hydra\2014-04-03\sale\107.html
Image 9 exists... creating
D:\dnmarchives\dnmarchives\hydra\2014-04-03\sale\108.html
Image 10 exists... creating
D:\dnmarchives\dnmarchives\hydra\2014-04-03\sale\109.html
Image 11 exists... creating
D:\dnmarchives\dnmarchives\hydra\2014-04-03\sale\11.html
Image 1

D:\dnmarchives\dnmarchives\hydra\2014-04-03\sale\189.html
Image 98 exists... creating
D:\dnmarchives\dnmarchives\hydra\2014-04-03\sale\19.html
Image 99 exists... creating
D:\dnmarchives\dnmarchives\hydra\2014-04-03\sale\190.html
Image 100 exists... creating
D:\dnmarchives\dnmarchives\hydra\2014-04-03\sale\191.html
Image 101 exists... creating
D:\dnmarchives\dnmarchives\hydra\2014-04-03\sale\192.html
Image 102 exists... creating
D:\dnmarchives\dnmarchives\hydra\2014-04-03\sale\193.html
Image 103 exists... creating
D:\dnmarchives\dnmarchives\hydra\2014-04-03\sale\194.html
Image 104 exists... creating
D:\dnmarchives\dnmarchives\hydra\2014-04-03\sale\195.html
Image 105 exists... creating
D:\dnmarchives\dnmarchives\hydra\2014-04-03\sale\196.html
Image 106 exists... creating
D:\dnmarchives\dnmarchives\hydra\2014-04-03\sale\197.html
Image 107 exists... creating
D:\dnmarchives\dnmarchives\hydra\2014-04-03\sale\198.html
Image 108 exists... creating
D:\dnmarchives\dnmarchives\hydra\2014-04-03\sa

Image 194 exists... creating
D:\dnmarchives\dnmarchives\hydra\2014-04-03\sale\99.html
Image 195 exists... creating
D:\dnmarchives\dnmarchives\hydra\2014-04-12\sale\10.html
Image 196 exists... creating
D:\dnmarchives\dnmarchives\hydra\2014-04-12\sale\102.html
Image 197 exists... creating
D:\dnmarchives\dnmarchives\hydra\2014-04-12\sale\103.html
Image 198 exists... creating
D:\dnmarchives\dnmarchives\hydra\2014-04-12\sale\104.html
Image 199 exists... creating
D:\dnmarchives\dnmarchives\hydra\2014-04-12\sale\105.html
Image 200 exists... creating
D:\dnmarchives\dnmarchives\hydra\2014-04-12\sale\106.html
Image 201 exists... creating
D:\dnmarchives\dnmarchives\hydra\2014-04-12\sale\107.html
Image 202 exists... creating
D:\dnmarchives\dnmarchives\hydra\2014-04-12\sale\108.html
Image 203 exists... creating
D:\dnmarchives\dnmarchives\hydra\2014-04-12\sale\109.html
Image 204 exists... creating
D:\dnmarchives\dnmarchives\hydra\2014-04-12\sale\11.html
Image 205 exists... creating
D:\dnmarchives\dn

Image 289 exists... creating
D:\dnmarchives\dnmarchives\hydra\2014-04-12\sale\203.html
Image 290 exists... creating
D:\dnmarchives\dnmarchives\hydra\2014-04-12\sale\204.html
Image 291 exists... creating
D:\dnmarchives\dnmarchives\hydra\2014-04-12\sale\205.html
Image 292 exists... creating
D:\dnmarchives\dnmarchives\hydra\2014-04-12\sale\206.html
Image 293 exists... creating
D:\dnmarchives\dnmarchives\hydra\2014-04-12\sale\207.html
Image 294 exists... creating
D:\dnmarchives\dnmarchives\hydra\2014-04-12\sale\208.html
Image 295 exists... creating
D:\dnmarchives\dnmarchives\hydra\2014-04-12\sale\209.html
Image 296 exists... creating
D:\dnmarchives\dnmarchives\hydra\2014-04-12\sale\21.html
Image 297 exists... creating
D:\dnmarchives\dnmarchives\hydra\2014-04-12\sale\210.html
Image 298 exists... creating
D:\dnmarchives\dnmarchives\hydra\2014-04-12\sale\211.html
Image 299 exists... creating
D:\dnmarchives\dnmarchives\hydra\2014-04-12\sale\212.html
Image 300 exists... creating
D:\dnmarchives\

Image 386 exists... creating
D:\dnmarchives\dnmarchives\hydra\2014-04-12\sale\31.html
Image 387 exists... creating
D:\dnmarchives\dnmarchives\hydra\2014-04-12\sale\32.html
Image 388 exists... creating
D:\dnmarchives\dnmarchives\hydra\2014-04-12\sale\33.html
Image 389 exists... creating
D:\dnmarchives\dnmarchives\hydra\2014-04-12\sale\34.html
Image 390 exists... creating
D:\dnmarchives\dnmarchives\hydra\2014-04-12\sale\35.html
Image 391 exists... creating
D:\dnmarchives\dnmarchives\hydra\2014-04-12\sale\36.html
Image 392 exists... creating
D:\dnmarchives\dnmarchives\hydra\2014-04-12\sale\37.html
Image 393 exists... creating
D:\dnmarchives\dnmarchives\hydra\2014-04-12\sale\38.html
Image 394 exists... creating
D:\dnmarchives\dnmarchives\hydra\2014-04-12\sale\40.html
Image 395 exists... creating
D:\dnmarchives\dnmarchives\hydra\2014-04-12\sale\41.html
Image 396 exists... creating
D:\dnmarchives\dnmarchives\hydra\2014-04-12\sale\42.html
Image 397 exists... creating
D:\dnmarchives\dnmarchive

...

Image 47569 has no name
D:\dnmarchives\dnmarchives\hydra\2014-10-27\sale\4066.html
Image 47570 has no name
D:\dnmarchives\dnmarchives\hydra\2014-10-27\sale\4067.html
Image 47571 has no name
D:\dnmarchives\dnmarchives\hydra\2014-10-27\sale\4068.html
Image 47572 has no name
D:\dnmarchives\dnmarchives\hydra\2014-10-27\sale\4069.html
Image 47573 has no name
D:\dnmarchives\dnmarchives\hydra\2014-10-27\sale\4070.html
Image 47574 has no name
D:\dnmarchives\dnmarchives\hydra\2014-10-27\sale\4071.html
Image 47575 has no name
D:\dnmarchives\dnmarchives\hydra\2014-10-27\sale\4072.html
Image 47576 has no name
D:\dnmarchives\dnmarchives\hydra\2014-10-27\sale\4073.html
Image 47577 has no name
D:\dnmarchives\dnmarchives\hydra\2014-10-27\sale\4074.html
Image 47578 has no name
D:\dnmarchives\dnmarchives\hydra\2014-10-27\sale\4074.html_Feedback_page=10
Image 47579 has no name
D:\dnmarchives\dnmarchives\hydra\2014-10-27\sale\4074.html_Feedback_page=11
Image 47580 has no name
D:\dnmarchives\dnmarchives\hy

Image 47664 has no name
D:\dnmarchives\dnmarchives\hydra\2014-10-27\sale\431.html
Image 47665 has no name
D:\dnmarchives\dnmarchives\hydra\2014-10-27\sale\431.html_Feedback_page=2
Image 47666 has no name
D:\dnmarchives\dnmarchives\hydra\2014-10-27\sale\432.html
Image 47667 has no name
D:\dnmarchives\dnmarchives\hydra\2014-10-27\sale\432.html_Feedback_page=2
Image 47668 has no name
D:\dnmarchives\dnmarchives\hydra\2014-10-27\sale\433.html
Image 47669 has no name
D:\dnmarchives\dnmarchives\hydra\2014-10-27\sale\433.html_Feedback_page=2
Image 47670 has no name
D:\dnmarchives\dnmarchives\hydra\2014-10-27\sale\434.html
Image 47671 has no name
D:\dnmarchives\dnmarchives\hydra\2014-10-27\sale\434.html_Feedback_page=2
Image 47672 has no name
D:\dnmarchives\dnmarchives\hydra\2014-10-27\sale\435.html
Image 47673 has no name
D:\dnmarchives\dnmarchives\hydra\2014-10-27\sale\435.html_Feedback_page=2
Image 47674 has no name
D:\dnmarchives\dnmarchives\hydra\2014-10-27\sale\436.html
Image 47675 has no

Image 47764 has no name
D:\dnmarchives\dnmarchives\hydra\2014-10-27\sale\6.html
Image 47765 has no name
D:\dnmarchives\dnmarchives\hydra\2014-10-27\sale\60.html
Image 47766 has no name
D:\dnmarchives\dnmarchives\hydra\2014-10-27\sale\61.html
Image 47767 has no name
D:\dnmarchives\dnmarchives\hydra\2014-10-27\sale\616.html
Image 47768 has no name
D:\dnmarchives\dnmarchives\hydra\2014-10-27\sale\63.html
Image 47769 has no name
D:\dnmarchives\dnmarchives\hydra\2014-10-27\sale\64.html
Image 47770 has no name
D:\dnmarchives\dnmarchives\hydra\2014-10-27\sale\644.html
Image 47771 has no name
D:\dnmarchives\dnmarchives\hydra\2014-10-27\sale\645.html
Image 47772 has no name
D:\dnmarchives\dnmarchives\hydra\2014-10-27\sale\646.html
Image 47773 has no name
D:\dnmarchives\dnmarchives\hydra\2014-10-27\sale\647.html
Image 47774 has no name
D:\dnmarchives\dnmarchives\hydra\2014-10-27\sale\65.html
Image 47775 has no name
D:\dnmarchives\dnmarchives\hydra\2014-10-27\sale\656.html
Image 47776 has no name

Image 47861 has no name
D:\dnmarchives\dnmarchives\hydra\2014-10-27\sale\796.html_Feedback_page=3
Image 47862 has no name
D:\dnmarchives\dnmarchives\hydra\2014-10-27\sale\796.html_Feedback_page=4
Image 47863 has no name
D:\dnmarchives\dnmarchives\hydra\2014-10-27\sale\796.html_Feedback_page=5
Image 47864 has no name
D:\dnmarchives\dnmarchives\hydra\2014-10-27\sale\796.html_Feedback_page=6
Image 47865 has no name
D:\dnmarchives\dnmarchives\hydra\2014-10-27\sale\796.html_Feedback_page=7
Image 47866 has no name
D:\dnmarchives\dnmarchives\hydra\2014-10-27\sale\796.html_Feedback_page=8
Image 47867 has no name
D:\dnmarchives\dnmarchives\hydra\2014-10-27\sale\796.html_Feedback_page=9
Image 47868 has no name
D:\dnmarchives\dnmarchives\hydra\2014-10-27\sale\797.html
Image 47869 has no name
D:\dnmarchives\dnmarchives\hydra\2014-10-27\sale\797.html_Feedback_page=10
Image 47870 has no name
D:\dnmarchives\dnmarchives\hydra\2014-10-27\sale\797.html_Feedback_page=11
Image 47871 has no name
D:\dnmarch

Image 47952 has no name
D:\dnmarchives\dnmarchives\hydra\2014-10-27\sale\908.html_Feedback_page=3
Image 47953 has no name
D:\dnmarchives\dnmarchives\hydra\2014-10-27\sale\909.html
Image 47954 has no name
D:\dnmarchives\dnmarchives\hydra\2014-10-27\sale\909.html_Feedback_page=2
Image 47955 has no name
D:\dnmarchives\dnmarchives\hydra\2014-10-27\sale\909.html_Feedback_page=3
Image 47956 has no name
D:\dnmarchives\dnmarchives\hydra\2014-10-27\sale\91.html
Image 47957 has no name
D:\dnmarchives\dnmarchives\hydra\2014-10-27\sale\910.html
Image 47958 has no name
D:\dnmarchives\dnmarchives\hydra\2014-10-27\sale\910.html_Feedback_page=2
Image 47959 has no name
D:\dnmarchives\dnmarchives\hydra\2014-10-27\sale\910.html_Feedback_page=3
Image 47960 has no name
D:\dnmarchives\dnmarchives\hydra\2014-10-27\sale\911.html
Image 47961 has no name
D:\dnmarchives\dnmarchives\hydra\2014-10-27\sale\911.html_Feedback_page=2
Image 47962 has no name
D:\dnmarchives\dnmarchives\hydra\2014-10-27\sale\911.html_Fee